# Overlap between chemical libraries

In [1]:
import pandas as pd

from rdkit import Chem
from rdkit.Chem import MolToInchiKey
from rdkit.Chem import PandasTools
from rdkit.Chem import Descriptors
from rdkit.Chem.rdMolDescriptors import CalcNumRings

import matplotlib.pyplot as plt
import seaborn as sns

Failed to find the pandas get_adjustment() function to patch
Failed to patch pandas - PandasTools will have limited functionality


In [2]:
import os
os.getcwd()

'/home/marina/Documents/DB/notebooks'

In [3]:
chebi = PandasTools.LoadSDF('/home/marina/Documents/DB/Libraries/original_libraries/chebi.sdf')
Antibacterial = PandasTools.LoadSDF('/home/marina/Documents/DB/Libraries/original_libraries/Antibacterial-Library-13880.sdf')
drugRepurposing_hub = pd.read_csv('/home/marina/Documents/DB/Libraries/original_libraries/drug_repurposing_hub.csv')
drugbank_smiles = pd.read_csv('/home/marina/Documents/DB/Libraries/original_libraries/drugbank_smiles.csv')

[11:11:20] Warning: ambiguous stereochemistry - linear bond arrangement - at atom 9 ignored
[11:11:20] Warning: ambiguous stereochemistry - linear bond arrangement - at atom 7 ignored
[11:11:20] Warning: ambiguous stereochemistry - linear bond arrangement - at atom 9 ignored
[11:11:20] Warning: ambiguous stereochemistry - linear bond arrangement - at atom 7 ignored
[11:11:20] Warning: ambiguous stereochemistry - linear bond arrangement - at atom 9 ignored
[11:11:20] Warning: ambiguous stereochemistry - linear bond arrangement - at atom 7 ignored
[11:11:20] Warning: ambiguous stereochemistry - linear bond arrangement - at atom 9 ignored
[11:11:20] Warning: molecule is tagged as 3D, but all Z coords are zero and 2D stereo markers have been found, marking the mol as 2D.
[11:11:20] Warning: ambiguous stereochemistry - linear bond arrangement - at atom 7 ignored
[11:11:20] Warning: ambiguous stereochemistry - linear bond arrangement - at atom 9 ignored
[11:11:20] Warning: ambiguous stereoch

In [4]:
chembl = pd.read_csv('/home/marina/Documents/DB/reference_cs/chembl_bitbirch_representatives_3.csv')

Molecule columns:
* chebi['INHIKEY']
* Antibacterial['InChI Key']
* drugRepurposing_hub['smiles']
*  drugbank_smiles['Smiles']
* chembl['SMILES']

## Add Inchikeys to missing libraries

In [ ]:
from rdkit import Chem
from rdkit.Chem.rdinchi import MolToInchiKey
import pandas as pd
from rdkit import Chem
from rdkit.Chem.rdinchi import MolToInchiKey
from rdkit.Chem.MolStandardize import rdMolStandardize
import pandas as pd

# --- Initialize RDKit Standardizers ---
# These are heavy objects, so we create them once globally
lfc = rdMolStandardize.LargestFragmentChooser()
normalizer = rdMolStandardize.Normalizer()
uncharger = rdMolStandardize.Uncharger()

def standardize_and_get_inchikey(mol, strip_stereo=True):
    """
    Standardize a molecule:
      - Largest fragment (strips salts/solvents)
      - Normalize & Uncharge
      - Optional stereochemistry stripping
    Returns (mol_clean, inchikey, smiles)
    """
    if mol is None:
        return None, None, None

    try:
        # 1. Largest fragment (remove salts/solvents)
        mol = lfc.choose(mol)

        # 2. Cleanup + normalize + uncharge
        mol = rdMolStandardize.Cleanup(mol)
        mol = normalizer.normalize(mol)
        mol = uncharger.uncharge(mol)

        # 3. Sanitize structure
        Chem.SanitizeMol(mol)

        # 4. Optionally collapse stereochemistry
        if strip_stereo:
            Chem.RemoveStereochemistry(mol)

        # 5. Generate InChIKey and Canonical SMILES
        ik = MolToInchiKey(mol)
        smiles = Chem.MolToSmiles(mol, canonical=True, isomericSmiles=not strip_stereo)
        
        return mol, ik, smiles
    except Exception as e:
        return None, None, None

def process_dataframe_chemistry(df, smiles_col, new_inchikey_col, strip_stereo=True):
    """
    Helper to apply standardization to a specific dataframe.
    """
    print(f"Processing {smiles_col}...")
    
    # Create initial Mol objects
    df['Mol_Temp'] = df[smiles_col].apply(lambda x: Chem.MolFromSmiles(str(x)) if pd.notna(x) else None)
    
    # Apply the standardization function
    # This returns a Series of tuples, which we expand into 3 columns
    results = df['Mol_Temp'].apply(lambda m: standardize_and_get_inchikey(m, strip_stereo=strip_stereo))
    
    # Assign results back to dataframe
    _, df[new_inchikey_col], df['Canonical_SMILES'] = zip(*results)
    
    # Cleanup
    df.drop('Mol_Temp', axis=1, inplace=True)
    
    valid_count = df[new_inchikey_col].count()
    print(f"Standardized {valid_count}/{len(df)} molecules.")
    return df

# --- Process drugRepurposing_hub ---
drugRepurposing_hub = process_dataframe_chemistry(
    drugRepurposing_hub,
    smiles_col='smiles',
    new_inchikey_col='INCHIKEY'
)

# --- Process drugbank_smiles ---
drugbank_smiles = process_dataframe_chemistry(
    drugbank_smiles,
    smiles_col='Smiles',
    new_inchikey_col='INCHIKEY'
)

chebi = process_dataframe_chemistry(
    chebi,
    smiles_col='SMILES',
    new_inchikey_col='INCHIKEY'
)
Antibacterial= process_dataframe_chemistry(
    Antibacterial,
    smiles_col='Smile',
    new_inchikey_col='INCHIKEY'
)
chembl= process_dataframe_chemistry(
    chembl,
    smiles_col='SMILES',
    new_inchikey_col='INCHIKEY'
)   


[11:12:46] Initializing Normalizer


Processing smiles...


[11:12:46] Can't kekulize mol.  Unkekulized atoms: 7 8 9 10 11 12 13 14 15
[11:12:46] Explicit valence for atom # 0 Cl, 2, is greater than permitted
[11:12:46] Explicit valence for atom # 0 Cl, 2, is greater than permitted
[11:12:47] Can't kekulize mol.  Unkekulized atoms: 0 1 2 3 4
[11:12:47] Can't kekulize mol.  Unkekulized atoms: 0 1 2 3 4
[11:12:47] Can't kekulize mol.  Unkekulized atoms: 6 7 8 9 10 11 12 13 16
[11:12:47] Can't kekulize mol.  Unkekulized atoms: 14 15 16 17 18 19 20 21 22
[11:12:47] Can't kekulize mol.  Unkekulized atoms: 16 17 18 19 20 21 22 23 24
[11:12:47] Can't kekulize mol.  Unkekulized atoms: 1 2 3 4 5 6 7 8 9
[11:12:47] Can't kekulize mol.  Unkekulized atoms: 0 1 2 3 4
[11:12:47] Explicit valence for atom # 1 Si, 8, is greater than permitted
[11:12:47] Can't kekulize mol.  Unkekulized atoms: 0 1 2 3 4
[11:12:47] Running LargestFragmentChooser
[11:12:47] Fragment: Cc1nc[nH]c1CC1CCc2c(C)c3ccccc3n2C1=O
[11:12:47] New largest fragment: Cc1nc[nH]c1CC1CCc2c(C)c3ccc

Standardized 7018/7030 molecules.
Processing Smiles...


[11:12:55] Explicit valence for atom # 13 Cl, 5, is greater than permitted
[11:12:55] SMILES Parse Error: syntax error while parsing: OS(O)(O)C1=CC=C(C=C1)C-1=C2\C=CC(=N2)\C(=C2/N\C(\C=C2)=C(/C2=N/C(/C=C2)=C(\C2=CC=C\-1N2)C1=CC=C(C=C1)S(O)(O)O)C1=CC=C(C=C1)S([O-])([O-])[O-])\C1=CC=C(C=C1)S(O)(O)[O-]
[11:12:55] SMILES Parse Error: Failed parsing SMILES 'OS(O)(O)C1=CC=C(C=C1)C-1=C2\C=CC(=N2)\C(=C2/N\C(\C=C2)=C(/C2=N/C(/C=C2)=C(\C2=CC=C\-1N2)C1=CC=C(C=C1)S(O)(O)O)C1=CC=C(C=C1)S([O-])([O-])[O-])\C1=CC=C(C=C1)S(O)(O)[O-]' for input: 'OS(O)(O)C1=CC=C(C=C1)C-1=C2\C=CC(=N2)\C(=C2/N\C(\C=C2)=C(/C2=N/C(/C=C2)=C(\C2=CC=C\-1N2)C1=CC=C(C=C1)S(O)(O)O)C1=CC=C(C=C1)S([O-])([O-])[O-])\C1=CC=C(C=C1)S(O)(O)[O-]'
[11:12:55] Explicit valence for atom # 19 O, 3, is greater than permitted
[11:12:55] Explicit valence for atom # 0 O, 3, is greater than permitted
[11:12:55] Unusual charge on atom 0 number of radical electrons set to zero
[11:12:55] Explicit valence for atom # 4 F, 2, is greater than permitted
[

Standardized 11915/11925 molecules.


In [ ]:
list(drugbank_smiles.columns)

['DrugBankId', 'Smiles', 'INCHIKEY-Canonical', 'Canonical_SMILES']

In [ ]:
import pandas as pd

# --- Setup for Integration ---
# Assuming these DataFrames are available and have the 'INCHIKEY' column:
# chembl, chebi, Antibacterial, drugRepurposing_hub, drugbank_smiles

# 1. Get the set of all unique INCHIKEYs from the filtered ChEMBL dataset
chembl_inchikeys = set(chembl['INCHIKEY'].dropna().str.strip())

# 2. Collect all the DataFrames to be integrated
datasets_to_integrate = {
    'ChEBI': chebi,
    'Antibacterial': Antibacterial,
    'Drug Repurposing Hub': drugRepurposing_hub,
    'DrugBank SMILES': drugbank_smiles
}

novel_molecules_list = []

print("## 🧬 Identifying Novel Molecules for Integration")

for name, df in datasets_to_integrate.items():
    # Ensure 'INCHIKEY' is standardized and clean for filtering
    df['INCHIKEY'] = df['INCHIKEY'].astype(str).str.strip()

    # Create a boolean mask: True for molecules NOT found in the ChEMBL set
    novel_mask = ~df['INCHIKEY'].isin(chembl_inchikeys)

    # Filter the DataFrame to keep only the novel molecules
    novel_df = df[novel_mask].copy()

    # Add a column to track the original source of the novel molecule
    novel_df['Original_Library'] = name
    
    # Select only the INCHIKEY and the new Original_Library column for aggregation
    # We strip down to avoid issues with different source column names (e.g., SMILES vs. ROMol)
    novel_df_subset = novel_df[['INCHIKEY', 'Original_Library']].copy()
    
    novel_molecules_list.append(novel_df_subset)
    
    print(f"| {name:<25} | Novel Molecules to Add: {len(novel_df_subset):<20} |")

# --- Combine all novel molecules into a single DataFrame ---
all_novel_molecules = pd.concat(novel_molecules_list, ignore_index=True)

# Important: Deduplicate the novel set based on INCHIKEY 
# If a molecule is novel but appears in two different libraries (e.g., ChEBI and DrugBank), 
# we keep only one entry and its first recorded library source.
unique_novel_molecules = all_novel_molecules.drop_duplicates(subset=['INCHIKEY'], keep='first')

print(f"\nTotal unique novel molecules across all libraries: {len(unique_novel_molecules)}")


# --- Final Integration: CONCATENATE ---

# 1. Add a source column to the original ChEMBL data
chembl['Original_Library'] = 'Filtered ChEMBL'

# 2. Harmonize ChEMBL for concatenation (INCHIKEY and Original_Library)
chembl_subset = chembl[['INCHIKEY', 'Original_Library']].copy()

# 3. Concatenate the original ChEMBL with the unique novel set
master_dataset_inchikeys = pd.concat([chembl_subset, unique_novel_molecules], ignore_index=True)

# Final check for total unique molecules
print(f"\n--- Integration Complete ---")
print(f"Original unique ChEMBL size: {len(chembl_subset)}")
print(f"Unique Novel Molecules added: {len(unique_novel_molecules)}")
print(f"Final Master Dataset Size (Unique INCHIKEYs): {len(master_dataset_inchikeys)}")
print("\nFinal Master Dataset Head:")
print(master_dataset_inchikeys.head())

In [ ]:
import pandas as pd
from rdkit import Chem
from rdkit.Chem import MolToSmiles

# --- 1. Setup DataFrames and Column Mapping ---

# Define the source DataFrames and their respective SMILES/Mol column names
all_source_data = [
    {'df': chembl,                 'inchikey_col': 'INCHIKEY', 'smiles_col': 'SMILES', 'mol_col': 'Mol', 'name': 'Filtered ChEMBL'},
    {'df': chebi,                  'inchikey_col': 'INCHIKEY', 'smiles_col': None,     'mol_col': 'ROMol', 'name': 'ChEBI'},
    {'df': Antibacterial,          'inchikey_col': 'INCHIKEY', 'smiles_col': None,     'mol_col': 'ROMol', 'name': 'Antibacterial'},
    {'df': drugRepurposing_hub,    'inchikey_col': 'INCHIKEY', 'smiles_col': 'smiles', 'mol_col': 'Mol', 'name': 'Drug Repurposing Hub'},
    {'df': drugbank_smiles,        'inchikey_col': 'INCHIKEY', 'smiles_col': 'Smiles', 'mol_col': 'Mol', 'name': 'DrugBank SMILES'}
]

# --- 2. Helper Function to get SMILES ---

def get_canonical_smiles(row, smiles_col, mol_col):
    """
    Returns the canonical SMILES string from either a SMILES column or a Mol column.
    Handles potential failure if both are None or invalid.
    """
    mol = None
    if smiles_col and pd.notna(row[smiles_col]):
        # Try converting from SMILES string (CSV sources)
        mol = Chem.MolFromSmiles(str(row[smiles_col]))
    elif mol_col in row and row[mol_col] is not None:
        # Use the existing RDKit Mol object (SDF sources)
        mol = row[mol_col]

    if mol:
        # Convert to canonical SMILES
        try:
            return MolToSmiles(mol, isomericSmiles=True, canonical=True)
        except:
            return None
    return None

# --- 3. Build the Master INCHIKEY-SMILES Lookup Table ---

master_lookup_list = []

print("## 🔍 Building INCHIKEY and Canonical SMILES Lookup Table")

for data in all_source_data:
    df = data['df'].copy()
    inchikey_col = data['inchikey_col']
    smiles_col = data['smiles_col']
    mol_col = data['mol_col']
    
    # Generate canonical SMILES for every row
    df['Canonical_SMILES'] = df.apply(
        lambda row: get_canonical_smiles(row, smiles_col, mol_col), axis=1
    )
    
    # Keep only the essential columns for lookup
    lookup_subset = df[[inchikey_col, 'Canonical_SMILES']].copy()
    lookup_subset.rename(columns={inchikey_col: 'INCHIKEY'}, inplace=True)
    
    # Clean and deduplicate the lookup set for this library
    lookup_subset.dropna(subset=['INCHIKEY', 'Canonical_SMILES'], inplace=True)
    lookup_subset.drop_duplicates(subset=['INCHIKEY'], keep='first', inplace=True)
    
    master_lookup_list.append(lookup_subset)

# Combine all lookups and deduplicate the FINAL list by INCHIKEY
smiles_lookup = pd.concat(master_lookup_list, ignore_index=True)
smiles_lookup.drop_duplicates(subset=['INCHIKEY'], keep='first', inplace=True)

print(f"Total unique (INCHIKEY, SMILES) pairs created: {len(smiles_lookup)}")


# --- 4. Merge the Lookup Table with the Integrated Dataset ---

# master_dataset_inchikeys is the integrated list from Step 6 (INCHIKEY, Original_Library)

master_dataset = pd.merge(
    master_dataset_inchikeys,
    smiles_lookup,
    on='INCHIKEY',
    how='left' # Keep all entries from our integrated list
)

# Final cleanup: drop any rows that somehow lost their SMILES during the merge 
# (Should be few, but good practice)
master_dataset.dropna(subset=['Canonical_SMILES'], inplace=True)

# Rename for clarity
master_dataset.rename(columns={'Canonical_SMILES': 'SMILES'}, inplace=True)

print(f"\n--- Final Master Dataset Creation Complete ---")
print(f"Final Master Dataset Size (with SMILES): {len(master_dataset)}")
print("Final Master Dataset Head:")
print(master_dataset.head())

In [ ]:
import pandas as pd
import os

# Assuming the 'master_dataset' DataFrame is available from the previous step 9

# --- 1. Prepare the DataFrame for Saving ---
# Select only the 'SMILES' column
smiles_only_df = master_dataset[['SMILES']].copy()

# --- 2. Define the File Name ---
output_filename = 'master_dataset_smiles.csv'

# --- 3. Save to CSV ---
smiles_only_df.to_csv(output_filename, index=False)

print(f"\n## ✅ Integration Complete: Master SMILES Saved")
print(f"The final list of unique SMILES has been successfully saved to: {output_filename}")
print(f"File contents verification (first 5 lines):")

# Verification: Print the head of the saved file to confirm format
with open(output_filename, 'r') as f:
    for i in range(5):
        print(f.readline().strip())

print(f"\nTotal SMILES saved: {len(smiles_only_df)}")